In [1]:
# Install necessary dependencies to run the notebook
#!python -m pip install -U pip pandas setuptools wheel pandas_profiling autogluon

/bin/sh: 1: python: not found


In [2]:
# Imports

from pandas_profiling import ProfileReport
from autogluon.tabular import TabularPredictor, TabularDataset
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import json

In [3]:
# Read the dataset from local file
df = pd.read_json('matchups.json', orient='records')

In [4]:
# HTML report for Exploratory Data Analysis
report = ProfileReport(df, title="Matchups Exploration", html={'style': {'full_width': True}})

report.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [5]:
# Display 5 first rows
df.head(5)

p_match_id  goldearned  totalminionskilled    win  kills  \
0     EUN1_2890026136_top        5506                 134  false      0   
1     EUN1_2890026136_top        6411                 126   true      3   
2  EUN1_2890026136_middle        4703                  89  false      1   
3  EUN1_2890026136_middle        6798                  99   true      6   
4  EUN1_2890026136_bottom        5074                 116  false      1   

   assists  deaths   champion  visionscore  \
0        1       3      Jayce            7   
1        3       0  TahmKench           10   
2        2       5    XinZhao            5   
3        2       4      Corki           11   
4        0       3   Aphelios            8   

                                               puuid  \
0  PBZ4iFFnVFISbV14iBj5RwL-VXbUs80lAyRSZQHG44gbkK...   
1  1Z6-2OQkYDtrSYXSss5gsjCFcvRK8omuWj9U0aXyZryRJ8...   
2  pyXq970IQz3gShPGxWtmkCGX7C7OowCjhESZABr-rbFcO-...   
3  gOOvKZ6ott8Xe5UmsotgotMSJM-FZvY2fwKUe9ta7wWDuc...   
4  iNZOIlwq4IimYqyX6dzvzPQt0TlP0wILwH0dw5OhwJ1FC1...   

   totaldamagedealttochampions summonername     gameversion  
0                         2350      Lethrox  11.15.389.2308  
1                         4796    marioetup  11.15.389.2308  
2                         6898         HEPl  11.15.389.2308  
3                         9870     Calaczek  11.15.389.2308  
4                         4985        Kayto  11.15.389.2308

In [6]:
# Display list of columns in the dataset
df.columns

Index(['p_match_id', 'goldearned', 'totalminionskilled', 'win', 'kills',
       'assists', 'deaths', 'champion', 'visionscore', 'puuid',
       'totaldamagedealttochampions', 'summonername', 'gameversion'],
      dtype='object')

In [7]:
# Get some stats from pandas (also findable in the AutoGluon HTML report)
df.describe()

goldearned  totalminionskilled         kills       assists  \
count  2.419192e+06        2.419192e+06  2.419192e+06  2.419192e+06   
mean   1.026814e+04        1.114065e+02  5.406807e+00  7.834544e+00   
std    3.598313e+03        7.733816e+01  4.413785e+00  5.671980e+00   
min    5.000000e+02        0.000000e+00  0.000000e+00  0.000000e+00   
25%    7.704000e+03        3.200000e+01  2.000000e+00  4.000000e+00   
50%    9.993000e+03        1.230000e+02  4.000000e+00  7.000000e+00   
75%    1.257100e+04        1.740000e+02  8.000000e+00  1.100000e+01   
max    3.641200e+04        5.070000e+02  4.900000e+01  5.200000e+01   

             deaths   visionscore  totaldamagedealttochampions  
count  2.419192e+06  2.419192e+06                 2.419192e+06  
mean   5.415834e+00  2.638441e+01                 1.473013e+04  
std    3.043467e+00  1.929920e+01                 1.380730e+06  
min    0.000000e+00  0.000000e+00                -2.147484e+09  
25%    3.000000e+00  1.400000e+01                 8.310000e+03  
50%    5.000000e+00  2.100000e+01                 1.367500e+04  
75%    7.000000e+00  3.200000e+01                 2.074100e+04  
max    3.200000e+01  2.590000e+02                 1.185980e+05

In [9]:
df.iloc[0]

p_match_id                                                   EUN1_2890026136_top
goldearned                                                                  5506
totalminionskilled                                                           134
win                                                                        false
kills                                                                          0
assists                                                                        1
deaths                                                                         3
champion                                                                   Jayce
visionscore                                                                    7
puuid                          PBZ4iFFnVFISbV14iBj5RwL-VXbUs80lAyRSZQHG44gbkK...
totaldamagedealttochampions                                                 2350
summonername                                                             Lethrox
gameversion                 

In [10]:
# Create AutoGluon Tabular Dataset 
# https://auto.gluon.ai/stable/tutorials/tabular_prediction/index.html
df = TabularDataset(df)

In [11]:
# drop columns we don't want (identifiers)
def _drop_column(df, col_name=list()):
    for x in col_name:
        try:
            df.drop([x],
                axis=1,
                inplace=True)
        except KeyError:
            print('{} already dropped from df'.format(x))
        

    return df


df = _drop_column(df, col_name=['puuid', 'summonerName'])

# Perform 80-20% train-test split
train = df.sample(frac=0.8, random_state=200) # random state is a seed value
test = df.drop(train.index)

In [12]:
# New look at the data - one example
df.iloc[0]

goldearned                               5506
totalminionskilled                        134
win                                     false
kills                                       0
assists                                     1
deaths                                      3
champion                                Jayce
visionscore                                 7
totaldamagedealttochampions              2350
gameversion                    11.15.389.2308
Name: 0, dtype: object

In [13]:
# Determine the label in our TabularDataset we want to predict
label = 'win'


# Create the tabular predictor with the target label by passing the training test
predictor = TabularPredictor(label=label,
                path='./autogluon_trained_models_liveclient_classifier').fit(train, time_limit=60)

Beginning AutoGluon training ... Time limit = 60s
AutoGluon will save models to "./autogluon_trained_models_liveclient_classifier/"
AutoGluon Version:  0.3.1
Train Data Rows:    1935354
Train Data Columns: 9
Preprocessing data ...
AutoGluon infers your prediction problem is: 'binary' (because only two unique label-values observed).
	2 unique label values:  ['true', 'false']
	If 'binary' is not the correct problem_type, please manually specify the problem_type argument in fit() (You may specify problem_type as one of: ['binary', 'multiclass', 'regression'])
Selected class <--> label mapping:  class 1 = true, class 0 = false
	Note: For your binary classification, AutoGluon arbitrarily selected which label-value represents positive (true) vs negative (false) class.
	To explicitly set the positive_class, either rename classes to 1 and 0, or specify positive_class in Predictor init.
Using Feature Generators to preprocess the data ...
Fitting AutoMLPipelineFeatureGenerator...
	Available Memo

In [14]:
# Make a test prediction from original test dataset
y_test = test[label] # we want 'win' column to be predicted


test_data_nolabel = test.drop(columns=[label])  # delete label column, also drop identifier column
# We have the testing dataset ready
test_data_nolabel.head(5)

goldearned  totalminionskilled  kills  assists  deaths     champion  \
2         4703                  89      1        2       5      XinZhao   
4         5074                 116      1        0       3     Aphelios   
6         4399                  24      2        2       5       Thresh   
14       22324                 217     26       12       5  MissFortune   
21       13888                 167      9        7      10       Veigar   

    visionscore  totaldamagedealttochampions     gameversion  
2             5                         6898  11.15.389.2308  
4             8                         4985  11.15.389.2308  
6            15                         2248  11.15.389.2308  
14           24                        69635  11.15.388.2387  
21           31                        22512   11.9.372.2066

In [15]:
# We load the model 
predictor = TabularPredictor.load('./autogluon_trained_models_liveclient_classifier')

# Predict test values
y_pred = predictor.predict(test_data_nolabel)
print("Predictions:  \n", y_pred)

# Evaluate prediction performance
perf = predictor.evaluate_predictions(y_true=y_test, y_pred=y_pred, auxiliary_metrics=True)

Predictions:  
 2          false
4          false
6          false
14          true
21         false
           ...  
2419155     true
2419157     true
2419159     true
2419182    false
2419191    false
Name: win, Length: 483838, dtype: object


Evaluation: accuracy on test data: 0.8375820005869733
Evaluations on test data:
{
    "accuracy": 0.8375820005869733,
    "balanced_accuracy": 0.8375865990712764,
    "mcc": 0.6751759127148671,
    "f1": 0.8377034283353986,
    "precision": 0.83546035015448,
    "recall": 0.8399585835576724
}


In [16]:
# Best performing models
predictor.leaderboard(test, silent=False)

                 model  score_test  score_val  pred_time_test  pred_time_val   fit_time  pred_time_test_marginal  pred_time_val_marginal  fit_time_marginal  stack_level  can_infer  fit_order
0             LightGBM    0.837582   0.834815        1.197913       0.115322  13.477807                 1.197913                0.115322          13.477807            1       True          4
1  WeightedEnsemble_L2    0.837582   0.834815        1.203413       0.143332  15.421995                 0.005500                0.028010           1.944188            2       True          5
2           LightGBMXT    0.835228   0.829803        0.861111       0.079495   9.230798                 0.861111                0.079495           9.230798            1       True          3
3       KNeighborsUnif    0.646063   0.644931        2.744013       0.238410   8.571524                 2.744013                0.238410           8.571524            1       True          1
4       KNeighborsDist    0.645685   0.646688

model  score_test  score_val  pred_time_test  pred_time_val  \
0             LightGBM    0.837582   0.834815        1.197913       0.115322   
1  WeightedEnsemble_L2    0.837582   0.834815        1.203413       0.143332   
2           LightGBMXT    0.835228   0.829803        0.861111       0.079495   
3       KNeighborsUnif    0.646063   0.644931        2.744013       0.238410   
4       KNeighborsDist    0.645685   0.646688        2.852881       0.264653   

    fit_time  pred_time_test_marginal  pred_time_val_marginal  \
0  13.477807                 1.197913                0.115322   
1  15.421995                 0.005500                0.028010   
2   9.230798                 0.861111                0.079495   
3   8.571524                 2.744013                0.238410   
4   8.563158                 2.852881                0.264653   

   fit_time_marginal  stack_level  can_infer  fit_order  
0          13.477807            1       True          4  
1           1.944188            2       True          5  
2           9.230798            1       True          3  
3           8.571524            1       True          1  
4           8.563158            1       True          2

In [17]:
# For the best model, display feature importance
predictor.feature_importance(test,
                            subsample_size=5000)

Computing feature importance via permutation shuffling for 9 features using 5000 rows with 3 shuffle sets...
	1.85s	= Expected runtime (0.62s per shuffle set)
	1.2s	= Actual runtime (Completed 3 of 3 shuffle sets)


importance    stddev   p_value  n  p99_high  \
deaths                         0.178800  0.000693  0.000003  3  0.182770   
assists                        0.147867  0.004041  0.000124  3  0.171025   
goldearned                     0.143133  0.004562  0.000169  3  0.169275   
totaldamagedealttochampions    0.050133  0.007338  0.003533  3  0.092184   
totalminionskilled             0.049667  0.002501  0.000422  3  0.063996   
kills                          0.039400  0.001709  0.000313  3  0.049192   
champion                       0.037133  0.006912  0.005676  3  0.076739   
visionscore                    0.001467  0.001405  0.106137  3  0.009516   
gameversion                    0.000400  0.001058  0.289958  3  0.006464   

                              p99_low  
deaths                       0.174830  
assists                      0.124709  
goldearned                   0.116992  
totaldamagedealttochampions  0.008083  
totalminionskilled           0.035338  
kills                        0.029608  
champion                    -0.002472  
visionscore                 -0.006583  
gameversion                 -0.005664

In [18]:
# Making predictions from incoming data
# goldearned, totalminionskilled, win, kills, assists, deaths, champion, visionscore, totaldamagedealttochampions, gameversion
# [5506, 134, false, 0, 1, 3, Jayce, 7, 2350, 11.15.389.2308]
data = [5506, 134, 0, 1, 3, 'Jayce', 7, 2350, '11.15.389.2308']

# From a list, load it into a dataframe and specify column names for consistency
test_d = pd.DataFrame([data], columns=['goldearned', 'totalminionskilled', 'kills', 'assists', 'deaths',
                                       'champion', 'visionscore', 'totaldamagedealttochampions', 'gameversion'])

In [19]:
#data = [91, 35, 0, 1080321, 2204, 390, 225, 0, 10, 0, 672, 0, 220, 0, 94, 0, 1047, 33]
#test_d = pd.DataFrame([data], columns=['magicResist', 'healthRegenRate', 'spellVamp', 'timestamp', 'maxHealth', 'moveSpeed', 'attackDamage', 'armorPenetrationPercent', 'lifesteal', 'abilityPower', 'resourceValue', 'magicPenetrationFlat', 'attackSpeed', 'currentHealth', 'armor', 'magicPenetrationPercent', 'resourceMax', 'resourceRegenRate'])


In [20]:
# Make prediction
predictor.predict(test_d)

# Print how probable each class is
print(predictor.predict_proba(test_d).iloc[0])

false    0.896259
true     0.103741
Name: 0, dtype: float64
